In [1]:
import tensorflow as tf

In [2]:
tf.constant([1])

<tf.Tensor: id=0, shape=(1,), dtype=int32, numpy=array([1], dtype=int32)>

# Binary Crossentropy Sanity Check

In [3]:
from tensorflow.keras.losses import BinaryCrossentropy

bce = BinaryCrossentropy()
y_true = tf.constant([[1]])
print(y_true.shape)
y_pred = tf.constant([[0.84]])
print(y_pred.shape)

bce(y_true, y_pred)

(1, 1)
(1, 1)


<tf.Tensor: id=43, shape=(), dtype=float32, numpy=0.17435327>

In [4]:
# implemented for single example only!
def binary_crossentropy(y_true, y_pred):
    loss = -tf.reduce_mean(y_true*tf.math.log(y_pred) + (1-y_true)*tf.math.log(1-y_pred))
    return loss

y_true = tf.constant(1, dtype=tf.float32)
y_pred = tf.constant(0.84, dtype=tf.float32)
binary_crossentropy(y_true, y_pred)

<tf.Tensor: id=57, shape=(), dtype=float32, numpy=0.17435342>

# Model Check

In [5]:
from fact_verification_system.classifier.models.textual_entailment import create_bert_model

In [6]:
model = create_bert_model(max_seq_length=64)
model.layers

In [13]:
max_seq_length =  64
def _parse_and_transform(serialized)-> dict:
    feature_description = {
        'input_word_ids': tf.io.FixedLenFeature([max_seq_length], tf.int64),
        'input_mask': tf.io.FixedLenFeature([max_seq_length], tf.int64),
        'segment_ids': tf.io.FixedLenFeature([max_seq_length], tf.int64),
        'target': tf.io.FixedLenFeature([], tf.int64)
    }
    example = tf.io.parse_single_example(serialized, feature_description)
    # transform
    target = example.pop('target')
    target = tf.reshape(target, ())
#     target = tf.cast(target, tf.float32)
    
    embeddings_dict = example
    for k, v in embeddings_dict.items():
        embeddings_dict[k] = tf.cast(v, tf.int32)

    target_dict = {'target': target}

    return (embeddings_dict, target_dict)

In [17]:
from fact_verification_system.classifier.scripts.train import _extract
import multiprocessing

suffix_train = "train_64_balanced_1000_samples.tfrecord"
file_pattern = "../dataset/tfrecords/" + suffix_train

ds_train = _extract(file_pattern)

num_cpus = multiprocessing.cpu_count()
ds_train = ds_train.map(_parse_and_transform, num_parallel_calls=num_cpus)

Reading from file pattern: ../dataset/tfrecords/train_64_balanced_1000_samples.tfrecord


Confirm? (y/n)
 y


Extracted all TFRecords with pattern ../dataset/tfrecords/train_64_balanced_1000_samples.tfrecord


In [18]:
model.compile(optimizer='adam', loss=bce, metrics=['accuracy'])
model.summary()

Model: "model"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_word_ids (InputLayer)     [(None, 64)]         0                                            
__________________________________________________________________________________________________
input_mask (InputLayer)         [(None, 64)]         0                                            
__________________________________________________________________________________________________
segment_ids (InputLayer)        [(None, 64)]         0                                            
__________________________________________________________________________________________________
keras_layer (KerasLayer)        [(None, 768), (None, 109482241   input_word_ids[0][0]             
                                                                 input_mask[0][0]             

In [52]:
x = next(iter(ds_train.batch(64)))

In [53]:
examples = ((x[0].get('input_mask'), x[0].get('input_word_ids'), x[0].get('segment_ids')))

In [54]:
preds = model.predict(examples, verbose=1)
preds

64/1 [==================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================================

array([[0.48722982],
       [0.4854541 ],
       [0.4976692 ],
       [0.5185944 ],
       [0.49833867],
       [0.4899739 ],
       [0.5094023 ],
       [0.509657  ],
       [0.49188018],
       [0.49415883],
       [0.4683441 ],
       [0.49850306],
       [0.47768974],
       [0.47768974],
       [0.46192384],
       [0.5010526 ],
       [0.4983601 ],
       [0.5216207 ],
       [0.4977231 ],
       [0.49324685],
       [0.49942976],
       [0.49445662],
       [0.4938993 ],
       [0.48802042],
       [0.5173138 ],
       [0.49243546],
       [0.4926082 ],
       [0.4977231 ],
       [0.49843293],
       [0.4924525 ],
       [0.4926082 ],
       [0.4926082 ],
       [0.4917287 ],
       [0.4930745 ],
       [0.49004233],
       [0.5098907 ],
       [0.49004233],
       [0.4908063 ],
       [0.483309  ],
       [0.5101681 ],
       [0.50240266],
       [0.500475  ],
       [0.5185944 ],
       [0.49404138],
       [0.48722982],
       [0.49445662],
       [0.5237998 ],
       [0.491

In [55]:
targets = tf.cast(x[1].get('target'), dtype=tf.float32)
targets

<tf.Tensor: id=25927, shape=(64,), dtype=float32, numpy=
array([1., 0., 0., 1., 1., 0., 0., 1., 1., 0., 0., 1., 0., 0., 0., 1., 1.,
       1., 0., 0., 1., 0., 0., 0., 0., 1., 1., 1., 1., 1., 1., 1., 0., 0.,
       0., 0., 0., 0., 0., 0., 0., 0., 0., 0., 1., 0., 0., 1., 0., 0., 1.,
       0., 0., 1., 0., 0., 0., 0., 1., 0., 0., 1., 1., 1.], dtype=float32)>

In [56]:
accumulator = 0
for (pred, target)  in zip(preds, targets):
    accumulator += binary_crossentropy(target, pred)

accumulator/len(targets)

<tf.Tensor: id=27018, shape=(), dtype=float32, numpy=0.6887974>

In [1]:
bce(y_true=targets, y_pred=examples)

NameError: name 'bce' is not defined

In [ ]:
import json
import pprint
pp = pprint.PrettyPrinter().pprint

path = "../dataset/train.json"
with open(path, 'r') as f:
    js = json.load(f)
    for j in js:
        if input("next?") == 'y':
            continue
        else:
            break
    

{'10': {'claim': 'Ireland does not have relatively low-lying mountains.',
        'evidence': [['Ireland', 10]],
        'label': 'REFUTES'},
 '100002': {'claim': 'The drama Dark Matter stars Taylor Schilling.',
            'evidence': [['Taylor_Schilling', 2], ['Taylor_Schilling', 0]],
            'label': 'SUPPORTS'},
 '100003': {'claim': 'In 1932, Prussia was taken over.',
            'evidence': [['Prussia', 30], ['Preußenschlag', 0]],
            'label': 'SUPPORTS'},
 '100004': {'claim': 'IZombie premiered in 2015.',
            'evidence': [['IZombie_-LRB-TV_series-RRB-', 2]],
            'label': 'SUPPORTS'},
 '100005': {'claim': 'Ronald Reagan had a nationality.',
            'evidence': [['Ronald_Reagan', 0]],
            'label': 'SUPPORTS'},
 '100006': {'claim': 'Samoa Joe wrestles professionally.',
            'evidence': [['Samoa_Joe', 0]],
            'label': 'SUPPORTS'},
 '100008': {'claim': 'University of Oxford is in the universe.',
            'evidence': [['Univers